# Project 2

Build a regression model for the band gap of two
dimensional non-magnetic materials. Including the
prediction of novel two-dimensional insulators.

## Import modules and models

In [43]:
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
#importando pacotes
from pymatgen.core.composition import *
import numpy as np
import pandas as pd
import ase.db
from pymatgen.core.composition import *
import numpy as np
import pandas as pd
from sklearn.model_selection import cross_val_score, GridSearchCV
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.model_selection import cross_val_score, GridSearchCV
from sklearn.linear_model import Ridge, Lasso
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor, BaggingRegressor
from sklearn.svm import SVR
import pickle

### Util functions for the models

In [44]:

def evaluate_regressors(X_train, Y_train, X_test, y_test):
    # Initialize regressors
    regressors = {
        'Ridge Regression': Ridge(),
        'Lasso Regression': Lasso(),
        'Decision Trees': DecisionTreeRegressor(),
        'Random Forest': RandomForestRegressor(),
        'Gradient Boosting': GradientBoostingRegressor(),
        'Support Vector Machines': SVR()
    }
    
    # Parameters for Grid Search
    params = {
        'Ridge Regression': {'alpha': [0.1, 1, 10]},
        'Lasso Regression': {'alpha': [0.1, 1, 10]},
        'Decision Trees': {'criterion': ['mse', 'friedman_mse']},
        'Random Forest': {'n_estimators': [10, 50]},
        'Gradient Boosting': {'n_estimators': [50, 100]},
        'Support Vector Machines': {'C': [0.1, 1, 10]}
    }
    
    # Store results
    results = {}
    
    for name, reg in regressors.items():
        print(f"Evaluating {name}...")
        
        # Cross Validation
        cv_score = cross_val_score(reg, X_train, Y_train, cv=5).mean()
        
        # Grid Search for Parameter Tuning
        grid_search = GridSearchCV(reg, params[name], cv=5)
        grid_search.fit(X_train, Y_train)
        
        # Bagging
        bagging = BaggingRegressor(reg)
        bagging.fit(X_train, Y_train)
        
        # Test the best estimator from Grid Search
        best_reg = grid_search.best_estimator_
        y_pred = best_reg.predict(X_test)
        
        # Calculate metrics
        mse = mean_squared_error(y_test, y_pred)
        r2 = r2_score(y_test, y_pred)
        
        # Store results
        results[name] = {
            'CV Score': cv_score,
            'Best Parameters': grid_search.best_params_,
            'Mean Squared Error': mse,
            'R2 Score': r2
        }
        
        # Print results
        print(f"CV Score: {cv_score}")
        print(f"Best Parameters: {grid_search.best_params_}")
        print(f"Mean Squared Error: {mse}")
        print(f"R2 Score: {r2}\n")
        
    return results

def save_best_model(results, X_train, Y_train, metric='R2 Score'):
    # Find the best model based on the given metric
    best_model_name = max(results, key=lambda k: results[k][metric])
    best_model_params = results[best_model_name]['Best Parameters']
    
    # Initialize regressors
    regressors = {
        'Ridge Regression': Ridge(),
        'Lasso Regression': Lasso(),
        'Decision Trees': DecisionTreeRegressor(),
        'Random Forest': RandomForestRegressor(),
        'Gradient Boosting': GradientBoostingRegressor(),
        'Support Vector Machines': SVR()
    }
    
    # Create and train the best model with best parameters
    best_model = regressors[best_model_name]
    best_model.set_params(**best_model_params)
    best_model.fit(X_train, Y_train)
    
    # Save the best model to a pickle file
    with open(f'{best_model_name}.pkl', 'wb') as f:
        pickle.dump(best_model, f)
        
    print(f"Saved {best_model_name} with {best_model_params} as a pickle file.")
    return best_model

### Get and preparing the data from db

In [45]:
df_atoms = pd.read_csv('Schleder2019_AtomicTable.csv')
df_atoms.set_index('Element', inplace = True)
dicio = df_atoms.to_dict('index')

# All properties in the atomic table
prop = ['Z',
        'Electronegativity',
        'IonizationPotential',
        'ElectronAffinity',
        'HOMO',
        'LUMO',
        'r_s_orbital',
        'r_p_orbital',
        'r_d_orbital',
        'r_atomic_nonbonded',
        'r_valence_lastorbital',
        'r_covalent',
        'Valence',
        'PeriodicColumn',
        'PeriodicColumn_upto18',
        'NumberUnfilledOrbitals',
        'Polarizability']

data = ase.db.connect('./c2db-2021-06-24.db')
rows = data.select()

In [46]:
## Listas que guardarão cada propriedade de cada elemento no composto por vez. ##
lista = []
pesos = []
stch = []
## Dicionário com as features estatísticas de todas as propriedades para cada material##
media_interm = {}

## Lista que guarda cada dicionário de cada material para levar para um dataframe ##
lista_completa = []

target='gap'
for row in rows:
    
    try:
        comp = Composition(row.formula).as_dict()
        elem = list(comp.items())
        
        ## Acrescentando a fórmula química ##
        media_interm['Material'] = row.formula
        
        ##
        media_interm['gap'] = row[target]
        
        ## Acrescentando o grupo espacial ##
        media_interm['Space group'] = row.spacegroup
        
        media_interm['Crystal Type'] = row.crystal_type
        
        ## Acrescentando o gap ##
        media_interm['Band gap'] = row.gap
        
        media_interm['stoichiometry'] = row.stoichiometry
    
        for i in prop:
            ## Lista com a propriedade de cada átomo ##
            for m in range(0, len(elem)):
                lista.append(dicio[elem[m][0]][i])
                pesos.append(elem[m][1])
                if (len(elem)==2):
                    stch.append(row.stoichiometry)
        
                
            
            ## Valor médio ##
            media_interm[f'media_{i}'] = np.mean(lista)

    
            ## Média ponderada ##
            avg = np.average(lista,weights=pesos)
            media_interm[f'media_pon_{i}'] = avg
    
            ## Valor máximo e mínimo ##
            max_prop = max(lista)
            min_prop = min(lista)
            media_interm[f'max_{i}'] = max_prop
            media_interm[f'min_{i}'] = min_prop
    
            ## Desvio padrão em relação a média ##
            media_interm[f'desvio_{i}'] = np.std(lista)
    
            ## Desvio padrão em relação a média ponderada ##
            sum_prop = 0
            for j in lista:
                sub2 = (j - avg)**2
                sum_prop = sum_prop + sub2
            media_interm[f'desvio_pon_{i}'] = np.sqrt(sum_prop/len(lista)) 
        
            lista.clear()
            pesos.clear()
        
        lista_completa.append(media_interm.copy())
    except Exception as error:
        print('Error: ', error)

print(set(stch))
    
print(len(lista_completa))
df = pd.DataFrame(lista_completa)
df.sample(20, random_state=100)       

Error:  'AtomsRow' object has no attribute 'gap'
Error:  'AtomsRow' object has no attribute 'gap'
Error:  'AtomsRow' object has no attribute 'gap'
{'A3B8', 'AB', 'A2B5', 'AB2', 'AB3', 'A3B4', 'AB12', 'A2B3', 'AB5', 'AB4'}
4053


Material       gap Space group     Crystal Type  Band gap  \
1446         CrAs2  0.000000       P-3m1       AB2-164-bd  0.000000   
2047         S8Si4  3.427869      P2_1/c         AB2-14-e  3.427869   
3517         HfSe2  1.687572       P-4m2       AB2-115-ag  1.687572   
719       Ag2MoSe4  0.695191        Cmm2    AB2C4-35-bcde  0.695191   
3149  Cu2Hg2Cl2Se2  0.833374      Pmc2_1       ABCD-26-ab  0.833374   
149        Mn3C2O2  0.000000       P-6m2  A2B2C3-187-bghi  0.000000   
2838        BiHfAs  0.000000        P3m1       ABC-156-ac  0.000000   
2337         Mo2O2  0.000000      P4/nmm        AB-129-bc  0.000000   
3562         NbCl2  0.000000       P-4m2       AB2-115-ag  0.000000   
1769        Mn2Cl6  0.038917         P-3       AB3-147-dg  0.038917   
3472          CoO2  0.000000       P-4m2       AB2-115-ag  0.000000   
427          CoBr2  0.347877       P-3m1       AB2-164-bd  0.347877   
3073     As4Ge4Se4  1.735405      P222_1       ABC-17-bce  1.735405   
388         Zn2Te2  0.544586       P-3m1         AB-164-d  0.544586   
4014     Cu2Cl2Te4  0.853349          P1         ABC2-1-a  0.853349   
3474          CoS2  0.000000       P-3m1       AB2-164-bd  0.000000   
2825      HfZr3Te8  0.213316          P1        AB3C8-1-a  0.213316   
1332         Ni2S2  0.000000      P4/nmm        AB-129-bc  0.000000   
2203       Sc4C3O2  0.000000       P-3m1   A2B3C4-164-bcd  0.000000   
2248        Ti2Br2  0.000000      P4/nmm        AB-129-bc  0.000000   

     stoichiometry    media_Z  media_pon_Z  max_Z  min_Z  ...  \
1446           AB2  28.500000    30.000000     33     24  ...   
2047           AB2  15.000000    15.333333     16     14  ...   
3517           AB2  53.000000    46.666667     72     34  ...   
719          AB2C4  41.000000    38.857143     47     34  ...   
3149          ABCD  40.000000    40.000000     80     17  ...   
149         A2B2C3  13.000000    14.714286     25      6  ...   
2838           ABC  62.666667    62.666667     83     33  ...   
2337            AB  25.000000    25.000000     42      8  ...   
3562           AB2  29.000000    25.000000     41     17  ...   
1769           AB3  21.000000    19.000000     25     17  ...   
3472           AB2  17.500000    14.333333     27      8  ...   
427            AB2  31.000000    32.333333     35     27  ...   
3073           ABC  33.000000    33.000000     34     32  ...   
388             AB  41.000000    41.000000     52     30  ...   
4014          ABC2  32.666667    37.500000     52     17  ...   
3474           AB2  21.500000    19.666667     27     16  ...   
2825         AB3C8  54.666667    50.666667     72     40  ...   
1332            AB  22.000000    22.000000     28     16  ...   
2203        A2B3C4  11.666667    13.111111     21      6  ...   
2248            AB  28.500000    28.500000     35     22  ...   

      max_NumberUnfilledOrbitals  min_NumberUnfilledOrbitals  \
1446                         6.0                         3.0   
2047                         4.0                         2.0   
3517                         8.0                         2.0   
719                          6.0                         1.0   
3149                         2.0                         0.0   
149                          5.0                         2.0   
2838                         8.0                         3.0   
2337                         6.0                         2.0   
3562                         7.0                         1.0   
1769                         5.0                         1.0   
3472                         3.0                         2.0   
427                          3.0                         1.0   
3073                         4.0                         2.0   
388                          2.0                         0.0   
4014                         2.0                         1.0   
3474                         3.0                         2.0   
2825                         8.0                         2.0   


### Turning labeled columns into numerical ones using encoding

The method fit_transform of labelencoder fit a label passed by parameter and return the respectively label encoded into a numerical value. These evaluations was necessary because the models can not be train using labeled values

In [47]:
labelencoder = LabelEncoder()

df['Material'] = labelencoder.fit_transform(df['Material'])
df['Space group'] = labelencoder.fit_transform(df['Space group'])
df['stoichiometry'] = labelencoder.fit_transform(df['stoichiometry'])

### Constructing the data for the model

In [48]:
X = df.drop(columns=['gap', 'Crystal Type', 'Band gap']).fillna(0)
Y_bandgap = df['Band gap']


In [49]:
X_train, X_test, Y_train, Y_test = train_test_split(X, Y_bandgap, test_size=0.25, random_state=30)

In [50]:
results = evaluate_regressors(X_train, Y_train, X_test, Y_test)

Evaluating Ridge Regression...


CV Score: 0.41649071453514985
Best Parameters: {'alpha': 0.1}
Mean Squared Error: 0.5683291136896507
R2 Score: 0.4766544166426656

Evaluating Lasso Regression...
CV Score: 0.1337790479170955
Best Parameters: {'alpha': 0.1}
Mean Squared Error: 0.7686841015435758
R2 Score: 0.2921576251335428

Evaluating Decision Trees...


/usr/local/lib/python3.10/dist-packages/sklearn/model_selection/_validation.py:425: FitFailedWarning: 
5 fits failed out of a total of 10.
The score on these train-test partitions for these parameters will be set to nan.
If these failures are not expected, you can try to debug them by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
5 fits failed with the following error:
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/sklearn/model_selection/_validation.py", line 732, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/usr/local/lib/python3.10/dist-packages/sklearn/base.py", line 1144, in wrapper
    estimator._validate_params()
  File "/usr/local/lib/python3.10/dist-packages/sklearn/base.py", line 637, in _validate_params
    validate_parameter_constraints(
  File "/usr/local/lib/python3.10/dist-packages/sklearn/utils/_pa

CV Score: 0.5093613170669705
Best Parameters: {'criterion': 'friedman_mse'}
Mean Squared Error: 0.6164451669235019
R2 Score: 0.43234677281100853

Evaluating Random Forest...
CV Score: 0.6749818190328151
Best Parameters: {'n_estimators': 50}
Mean Squared Error: 0.3350430829268636
R2 Score: 0.6914757427331983

Evaluating Gradient Boosting...
CV Score: 0.6569898066038697
Best Parameters: {'n_estimators': 100}
Mean Squared Error: 0.3391991196918261
R2 Score: 0.6876486583329409

Evaluating Support Vector Machines...
CV Score: -0.1293364601900032
Best Parameters: {'C': 10}
Mean Squared Error: 1.133916432970823
R2 Score: -0.0441663866891735



In [51]:
model_to_use = save_best_model(results, X_train, Y_train)

Saved Random Forest with {'n_estimators': 50} as a pickle file.


## Deploying the model

### Creating a new dataset to predict using the model
Here, we'll doing exact the same steps that we do in project 1.

In [52]:
STCH=['A2B3', 'AB2', 'A2B2']
PROT=['P-3m1','P-6m2','Pmmn','P1',]

TM=['Sc','Ti','Cu','Zn','Zr','Nb','Mo','Ru','Rh','Pd','Ag','Cd','Hf','Ta','W','Re','Os','Ir','Pt','Au']
HL=['F','Cl','Br','I','S','Se','Te']

elem=list(Composition(STCH[0]).as_dict().items())
n=0
new = {}
lista = []

for i in range(len(STCH)):
    elem=list(Composition(STCH[i]).as_dict().items())
    for j in range(len(TM)):
        for k in range(len(HL)):
            for l in range(len(PROT)):
                
                if(int(elem[0][1])==1):
                    if(int(elem[1][1])==1):
                        new['Material']=("%s%s"%(TM[j],HL[k]))
                    else:
                        new['Material']=("%s%s%s"%(TM[j],HL[k],str(int(elem[1][1]))))
                    
                    
                else:
                    if(int(elem[1][1])==1):
                        new['Material']=("%s%s%s%s"%(TM[j],str(int(elem[0][1])),HL[k]))
                    else:
                        new['Material']=("%s%s%s%s"%(TM[j],str(int(elem[0][1])),HL[k],str(int(elem[1][1]))))
                
                
                new['Prototype']=(PROT[l])
                new['stoichiometry'] = STCH[i]
                lista.append(new.copy())
                n+=1
new_materials = pd.DataFrame(lista)
new_materials.sample(10, random_state=100)            
new_materials

Material Prototype stoichiometry
0       Sc2F3     P-3m1          A2B3
1       Sc2F3     P-6m2          A2B3
2       Sc2F3      Pmmn          A2B3
3       Sc2F3        P1          A2B3
4      Sc2Cl3     P-3m1          A2B3
...       ...       ...           ...
1675   Au2Se2        P1          A2B2
1676   Au2Te2     P-3m1          A2B2
1677   Au2Te2     P-6m2          A2B2
1678   Au2Te2      Pmmn          A2B2
1679   Au2Te2        P1          A2B2

[1680 rows x 3 columns]

In [53]:
## Listas que guardarão cada propriedade de cada elemento no composto por vez. ##
lista = []
pesos = []

## Dicionário com as features estatísticas de todas as propriedades para cada material##
media_interm = {}

## Lista que guarda cada dicionário de cada material para levar para um dataframe ##
lista_completa = []


for i in range(0,100000):
    try:
        formula = new_materials.iloc[i]['Material']
        comp = Composition(formula).as_dict()
        elem = list(comp.items())
        
        ## Acrescentando a fórmula química ##
        media_interm['Material'] = formula
        
        ## Acrescentando o grupo espacial ##
        media_interm['Space group'] = new_materials.iloc[i]['Prototype']
        media_interm['stoichiometry'] = new_materials.iloc[i]['stoichiometry']
    
        for i in prop:
            ## Lista com a propriedade de cada átomo ##
            for m in range(0, len(elem)):
                lista.append(dicio[elem[m][0]][i])
                pesos.append(elem[m][1])
            
            ## Valor médio ##
            media_interm[f'media_{i}'] = np.mean(lista)

    
            ## Média ponderada ##
            avg = np.average(lista,weights=pesos)
            media_interm[f'media_pon_{i}'] = avg
    
            ## Valor máximo e mínimo ##
            max_prop = max(lista)
            min_prop = min(lista)
            media_interm[f'max_{i}'] = max_prop
            media_interm[f'min_{i}'] = min_prop
    
            ## Desvio padrão em relação a média ##
            media_interm[f'desvio_{i}'] = np.std(lista)
    
            ## Desvio padrão em relação a média ponderada ##
            sum_prop = 0
            for j in lista:
                sub2 = (j - avg)**2
                sum_prop = sum_prop + sub2
            media_interm[f'desvio_pon_{i}'] = np.sqrt(sum_prop/len(lista)) 
        
            lista.clear()
            pesos.clear()
        
        lista_completa.append(media_interm.copy())
    except Exception as error:
        print('Error: ', error)


Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional index

The errors above are caught because we are using a range(0,100000) in the first for-loop. In the example on the github these errors not ocurred due the "Except: pass" clasule. Here, we are using a expcetion treatment.

In [54]:
df = pd.DataFrame(lista_completa)
df.sample(10, random_state=100)

df

Material Space group stoichiometry  media_Z  media_pon_Z  max_Z  min_Z  \
0       Sc2F3       P-3m1          A2B3     15.0         13.8     21      9   
1       Sc2F3       P-6m2          A2B3     15.0         13.8     21      9   
2       Sc2F3        Pmmn          A2B3     15.0         13.8     21      9   
3       Sc2F3          P1          A2B3     15.0         13.8     21      9   
4      Sc2Cl3       P-3m1          A2B3     19.0         18.6     21     17   
...       ...         ...           ...      ...          ...    ...    ...   
1675   Au2Se2          P1          A2B2     56.5         56.5     79     34   
1676   Au2Te2       P-3m1          A2B2     65.5         65.5     79     52   
1677   Au2Te2       P-6m2          A2B2     65.5         65.5     79     52   
1678   Au2Te2        Pmmn          A2B2     65.5         65.5     79     52   
1679   Au2Te2          P1          A2B2     65.5         65.5     79     52   

      desvio_Z  desvio_pon_Z  media_Electronegativity  ...  \
0          6.0      6.118823                    2.670  ...   
1          6.0      6.118823                    2.670  ...   
2          6.0      6.118823                    2.670  ...   
3          6.0      6.118823                    2.670  ...   
4          2.0      2.039608                    2.260  ...   
...        ...           ...                      ...  ...   
1675      22.5     22.500000                    2.545  ...   
1676      13.5     13.500000                    2.320  ...   
1677      13.5     13.500000                    2.320  ...   
1678      13.5     13.500000                    2.320  ...   
1679      13.5     13.500000                    2.320  ...   

      max_NumberUnfilledOrbitals  min_NumberUnfilledOrbitals  \
0                            9.0                         1.0   
1                            9.0                         1.0   
2                            9.0                         1.0   
3                            9.0                         1.0   
4                            9.0                         1.0   
...                          ...                         ...   
1675                         2.0                         1.0   
1676                         2.0                         1.0   
1677                         2.0                         1.0   
1678                         2.0                         1.0   
1679                         2.0                         1.0   

      desvio_NumberUnfilledOrbitals  desvio_pon_NumberUnfilledOrbitals  \
0                               4.0                           4.079216   
1                               4.0                           4.079216   
2                               4.0                           4.079216   
3                               4.0                           4.079216   
4                               4.0                           4.079216   
...                             ...                                ...   
1675                            0.5                           0.500000   
1676                            0.5                           0.500000   
1677                            0.5                           0.500000   
1678                            0.5                           0.500000   
1679                            0.5                           0.500000   

      media_Polarizability  media_pon_Polarizability  max_Polarizability  \
0                   55.350                    45.020               107.0   
1                   55.350                    45.020               107.0   
2                   55.350                    45.020               107.0   
3                   55.350                    45.020               107.0   
4                   60.785                    51.542               107.0   
...                    ...                       ...                 ...   
1675                31.170                    31.170                36.1   
1676                36.550                   

## Getting the data for classification project (project 1)

In [55]:
df_classifications = pd.read_csv('Result_Prediction_Metal_Insulator_Classificator.csv')
df_classifications = df_classifications.drop(columns=['Unnamed: 0'])
df_classifications

Sc2F3⁻P-3m1  Sc2F3⁻P-6m2  Sc2F3⁻Pmmn  Sc2F3⁻P1  Sc2Cl3⁻P-3m1  Sc2Cl3⁻P-6m2  \
0            0            0           0         0             0             0   

   Sc2Cl3⁻Pmmn  Sc2Cl3⁻P1  Sc2Br3⁻P-3m1  Sc2Br3⁻P-6m2  ...  Au2S2⁻Pmmn  \
0            0          0             0             0  ...           0   

   Au2S2⁻P1  Au2Se2⁻P-3m1  Au2Se2⁻P-6m2  Au2Se2⁻Pmmn  Au2Se2⁻P1  Au2Te2⁻P-3m1  \
0         0             0             0            0          0             0   

   Au2Te2⁻P-6m2  Au2Te2⁻Pmmn  Au2Te2⁻P1  
0             0            0          0  

[1 rows x 1680 columns]

In [56]:
predictions = []

for column in df_classifications.columns:
    for pred in df_classifications[column]:
        predictions.append(pred)

predictions = np.array(predictions)

predictions

array([0, 0, 0, ..., 0, 0, 0])

### Filtering only the insulators

In [57]:
df = df[[bool(pred) for pred in predictions]]

In [58]:
materials = df['Material']
spacegroups = df['Space group']

In [59]:
df['Material'] = labelencoder.fit_transform(df['Material'])
df['Space group'] = labelencoder.fit_transform(df['Space group'])
df['stoichiometry'] = labelencoder.fit_transform(df['stoichiometry'])

prediction = model_to_use.predict(df)

prediction

df['Band gap'] = prediction

/tmp/ipykernel_5267/2684735056.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Material'] = labelencoder.fit_transform(df['Material'])
/tmp/ipykernel_5267/2684735056.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Space group'] = labelencoder.fit_transform(df['Space group'])
/tmp/ipykernel_5267/2684735056.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentati

In [60]:
df.to_csv('Result_Prediction_BANDGAP.csv')